In [1]:
import requests
import re
from bs4 import BeautifulSoup
from lxml import etree
from pandas import DataFrame
from IPython.display import display

In [2]:
urls = ['http://finance.jxufe.edu.cn/news-list-jiangshi.html', 'http://finance.jxufe.edu.cn/news-list-jiangshi-2.html']

teacher_list = []

for url in urls:
    html = requests.get(url)
    html.encoding = 'utf-8'
    html_bytes = html.content
    soup = BeautifulSoup (html_bytes , 'html.parser')
    div_people_list = soup.find_all ('div' , attrs = {'class' : 'textlist'})
    for item in div_people_list:
        info = item.find_all('a')
        teacher_list.append([info[0].get_text(), info[0]['href']])

jiang_shi = []
for teacher_id in teacher_list:
    url = teacher_id[1]
    teacher_info = requests.get(url)
    teacher_info.encoding = 'utf-8'
    teacher_info = teacher_info.content
    soup = BeautifulSoup (teacher_info , 'html.parser')
    people_info = soup.find('div' , attrs = {'class' : 'ne_main_R'})
    all_info = people_info.find_all('p')
    
    collected_info = []
    for item in all_info[1:]:
        temp_info = item.get_text()
        if temp_info == '' or temp_info == ' ':
            continue
        temp_info = temp_info.replace(' ', '')
        temp_info = temp_info.replace('\u3000', '')
        temp_info = temp_info.replace('\xa0', '')
        temp_info = temp_info.replace('u', '')
        collected_info.append(temp_info)
    teacher = {}
    
    other = ''
    for item in collected_info:
        if re.findall('姓名',item):
            teacher['教师姓名'] = item.split('：')[1]
        elif re.findall('性别',item):
            teacher['性别'] = item.split('：')[1]
        elif re.findall('出生年月',item):
            teacher['出生年月'] = item.split('：')[1]
        elif re.findall('政治面貌',item):
            teacher['政治面貌'] = item.split('：')[1]
        elif re.findall('毕业院校',item):
            teacher['毕业院校'] = item.split('：')[1]
        elif re.findall('毕业专业',item):
            teacher['毕业专业'] = item.split('：')[1]
        elif re.findall('职务',item):
            teacher['职务'] = item.split('：')[1]
        elif re.findall('职称',item):
            teacher['职称'] = item.split('：')[1]
        elif re.findall('邮箱',item):
            teacher['邮箱'] = item.split('：')[1]
        else:
            other =  other + ' ' + item
    teacher['其它经历'] = other
    jiang_shi.append(teacher)
    

In [3]:
df1 = DataFrame(columns=('教师姓名','性别','政治面貌','毕业院校','毕业专业','职称','邮箱'))
for i in range(0, len(jiang_shi)):
    for key in jiang_shi[i]:
        if key != '其它经历' and key != '出生年月'and key != '职务':
            df1.loc[i, key] = jiang_shi[i][key]
display(df1)

教师姓名 性别  政治面貌         毕业院校        毕业专业        职称                        邮箱
0    段梅  女  中共党员         厦门大学         金融学        讲师           jxfe_dm@126.com
1    甘柳  男    群众  湖南大学金融与统计学院       金融学博士        教师         ganli2016@163.com
2    高祥  男    群众          NaN       宏观经济学        讲师          994500626@qq,com
3   何燕婷  女  中共党员         武汉大学         投资学        讲师      heyanting-77@163.com
4    胡军  男  中共党员       上海财经大学        公司金融        讲师           hoojn98@126.com
5   赖少杰  男  民革党员       肯特州立大学         金融学        讲师        shaojielai@126.com
6    李佳  男                                                      jia31@msn.com
7    李静  女  中共党员   匈牙利圣伊斯特万大学        金融经济        讲师  jasmine_intl@foxmail.com
8   李卫民     中共党员       江西财经大学    金融学（管理学）        讲师       liweimin881@sina.cn
9   刘黎平  男  中共党员         厦门大学        国际金融        讲师          286872863@qq.com
10  刘泽民  男  中共党员                                 讲师          827030973@qq.com
11  牛子雨       群众      英国斯特林大学       银行与金融        讲师         2295015739@qq.com
12   寿晖  男                                                13970014516@163.com
13   王慧     民建会员       江西财经大学         金融学        讲师      wang_hir2002@163.com
14   王青  女    群众      新西兰梅西大学        公司金融        讲师    sophiewang3214@163.com
15  王清生  男    群众         云南大学  概率论与数理统计专业        讲师   ynwangqingsheng@163.com
16   文艺  男    群众         南开大学         金融学        讲师           mrwenyi@163.com
17  吴艳艳  女             江西财经大学         金融学        讲师           wyyjrxy@163.com
18   杨超  男   NaN       西南财经大学         NaN  讲师/硕士生导师          826594365@qq.com
19   周闯  男  中共党员         武汉大学         金融学        讲师       zhochang@jxfe.ed.cn
20  邹永杰  男    群众       北京师范大学   金融系统分析与集成        讲师         zyj918303@163.com
21  吴燕丰  男    群众         复旦大学     管理科学与工程       NaN                       NaN